In [1]:
%load_ext autoreload

%autoreload 2

In [2]:
import simpleaudio as sa
import numpy as np
import os

import IPython.display as ipd

In [23]:
from pySynth.io.IO import *
from pySynth.io.player import *
from pySynth.control.stream import *
from pySynth.synth.effect import *
from pySynth.synth.filter import *
from pySynth.synth.synthesizer import *
from pySynth.synth.oscillator import *

In [24]:
midi_filepath = "test.mid"
midi_func = ReadMIDI(midi_filepath)
midi_ls = midi_func()

print(midi_ls)

fs = 44100

[[60, 0.0, 0.5], [64, 0.5, 1.0], [67, 1.0, 1.5], [64, 2.0, 2.5], [62, 2.5, 2.75], [60, 2.75, 3.0], [62, 3.0, 3.125], [60, 3.25, 3.375], [60, 3.5, 4.0], [69, 4.0, 4.5], [67, 4.5, 5.0], [62, 5.0, 5.25], [64, 5.25, 5.5], [62, 5.5, 5.75], [62, 5.75, 6.0], [64, 6.0, 6.25], [60, 6.5, 7.0], [62, 7.0, 7.5], [60, 7.5, 8.0]]


# Oscillator with MIDI Input

In [12]:
stream = MIDIStream("triangle") # Support sine, triangle and square wave
audio = stream.render(midi_ls)
ipd.Audio(audio, rate = fs)

# OSC with ADSR

In [13]:
adsr = ADSR()
stream = MIDIStream("triangle", adsr = adsr)
audio = stream.render(midi_ls)
ipd.Audio(audio, rate = fs)

# One Effect Chain

In [17]:
# Uncomment any effect or filter you want. 
# You can also change the order, change the parameter, and duplicate effect/filter in the Chain.

effects = EffectChain(
#     Reverb(gain_dry = 1, gain_wet = 1, reverb_type = "hall"),
    Delay(delayTime = 0.25),
     Chorus(fmod = 1.5, BL=1.0, FF=0.7),
#     Vibrato(maxDelaySamps = 100, feedback = -0.7),
    LowPass(Low_Band=800),
#     BandPass(Low_Band = 400, High_Band = 800),
    Wahwah(min_cutoff=300, max_cutoff=4000, rate=10000, damp=0.2) 
)

adsr = ADSR()
stream = MIDIStream("triangle", adsr = adsr)
audio = stream.render(midi_ls)
audio = effects(audio)

ipd.Audio(audio, rate = fs)

# Multiple Effect Chains & AddSynth

In [18]:
effects1 = EffectChain(
    Reverb(1,1,"hall"),
    Delay(delayTime = 0.25),
)

effects2 =  EffectChain(
    Chorus(),
    BandPass(Low_Band=400)
)

stream = MIDIStream("triangle")
audio = stream.render(midi_ls)
audio1 = effects1(audio)
audio2 = effects2(audio)

synth = AddSynth(
    audio1,
    audio2)

audio = synth()

ipd.Audio(audio, rate = fs)

# Wave Table

### Use three osc for one note

In [19]:
adsr = ADSR()

stream1 = MIDIStream("sine",adsr)
stream2 = MIDIStream("triangle")
stream3 = MIDIStream("square",adsr)

wt = WaveTable(
    stream1,
    stream2,
    stream3
)

audio = wt(midi_ls)
ipd.Audio(audio, rate = fs)

# Play the music using Player object, not Jupyter Notebook's Audio gadget

In [25]:
player = Player(sr = fs, bit_depth = 16)
player.play(audio)

# Save the audio into a file

In [27]:
saveAudio("example.wav", audio, sr = fs, format = "wav", bit_depth = 16)